In [34]:
import pandas as pd

In [35]:
df = pd.read_csv("step5.csv", encoding='utf-8-sig', sep=';')

In [ ]:
import numpy as np
from sklearn.metrics import classification_report, confusion_matrix

classification_label_set = {
    "auto": 0,
    "Business and Industry": 1,
    "Crime and Justice": 2,
    "Disaster and Emergency News": 3,
    "Economics and Finance": 4,
    "Education": 5,
    "Entertainment and Culture": 6,
    "Environment and Climate": 7,
    "Family and Relationships": 8,
    "Fashion": 9,
    "Food and Drink": 10,
    "Health and Medicine": 11,
    "Transportation and Infrastructure": 12,
    "Mental Health and Wellness": 13,
    "Politics and Government": 14,
    "Religion": 15,
    "Sports": 16,
    "Travel and Leisure": 17,
    "Technology and Science": 18
}


classification_label_dict = {idx: label for idx, label in enumerate(classification_label_set)}
classification_label_dict_to_index = {v: k for k, v in classification_label_dict.items()}


ner_label_set = ["PAD","O",
    "B-ORG", "I-ORG", "B-PERSON", "I-PERSON", "B-CARDINAL", "I-CARDINAL",
    "B-GPE", "I-GPE", "B-DATE", "I-DATE", "B-ORDINAL", "I-ORDINAL",
    "B-PERCENT", "I-PERCENT", "B-LOC", "I-LOC", "B-NORP", "I-NORP",
    "B-MONEY", "I-MONEY", "B-TIME", "I-TIME", "B-EVENT", "I-EVENT",
    "B-PRODUCT", "I-PRODUCT", "B-FAC", "I-FAC", "B-QUANTITY", "I-QUANTITY"
]


ner_label_dict = {label: idx for idx, label in enumerate(ner_label_set)}

ner_label_dict_reverse = {idx: label for label, idx in ner_label_dict.items()}

In [37]:
from transformers import AutoTokenizer
model_name = "nlpaueb/bert-base-greek-uncased-v1"
tokenizer = AutoTokenizer.from_pretrained(model_name)


In [38]:
df.head(1)

url  \
0  https://www.sport-fm.gr/article/o-roueda-sti-S...   

                                  title  \
0  Ο πρώην της Ferrari πήγε στην Sauber   

                                                text label  \
0  Τον πρώην επικεφαλής στρατηγικής και αθλητικό ...  auto   

                                          clean_text  \
0  Ο πρώην της Ferrari πήγε στην Sauber Τον πρώην...   

                                         ner_results  \
0  [{'text': 'ferrari', 'type': 'ORG', 'start_pos...   

                                        ner_sequence  \
0  [{'word': 'Ο', 'entity': 'O'}, {'word': 'πρώην...   

                                               words  \
0  ['Ο', 'πρώην', 'της', 'Ferrari', 'πήγε', 'στην...   

                                            entities  \
0  ['O', 'O', 'O', 'B-ORG', 'O', 'O', 'B-ORG', 'O...   

                                     entities_parsed  \
0  ['O', 'O', 'O', 'B-ORG', 'O', 'O', 'B-ORG', 'O...   

                                    entities_numbers  label_numbers  
0  [1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, ...              0

In [39]:
df['entities_numbers'] = df['entities_numbers'].apply(ast.literal_eval)
df['labels'] = df['label_numbers']
df['ner_labels'] = df['entities_numbers']

In [40]:
import numpy as np
import random
import torch

def set_seed(seed=42):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)


In [ ]:
import torch
from torch.utils.data import DataLoader, Dataset
import ast
import pandas as pd
from sklearn.model_selection import train_test_split
from transformers import AutoTokenizer

ner_label_dict = {label: idx for idx, label in enumerate(ner_label_set)}
ner_label_dict_reverse = {v: k for k, v in ner_label_dict.items()}

def chunk_list(items, chunk_size):
    """Splits the list 'items' into chunks of size 'chunk_size'."""
    return [items[i:i + chunk_size] for i in range(0, len(items), chunk_size)]

class NewsNERChunkedDataset(Dataset):
    def __init__(self, dataframe, tokenizer, word_chunk_size=412, target_token_length=512):
        self.tokenizer = tokenizer
        self.word_chunk_size = word_chunk_size
        self.target_token_length = target_token_length
        
        self.samples = []
        for _, row in dataframe.iterrows():
            words = row['words']
            if isinstance(words, str):
                words = ast.literal_eval(words)
            
            # Classification label
            label_class = int(row['labels'])
            
            # NER labels
            ner_labels_val = row['ner_labels']
            if isinstance(ner_labels_val, str):
                ner_labels_val = ast.literal_eval(ner_labels_val)
            
            # Split into chunks
            word_chunks = chunk_list(words, self.word_chunk_size)
            ner_label_chunks = chunk_list(ner_labels_val, self.word_chunk_size)
            
            for word_chunk, ner_chunk in zip(word_chunks, ner_label_chunks):
                encoding = self.tokenizer(
                    word_chunk,
                    is_split_into_words=True,
                    truncation=True,
                    max_length=self.target_token_length,
                    padding='max_length',
                    return_offsets_mapping=True
                )
                
                raw_word_ids = encoding.word_ids() 
                transformed_word_ids = []
                for w_id in raw_word_ids:
                    if w_id is None:
                        transformed_word_ids.append(-100)      
                    else:
                        transformed_word_ids.append(w_id + 1)  

                aligned_labels = []
                previous_word_idx = None
                for w_idx in encoding.word_ids():
                    if w_idx is None:
                        aligned_labels.append(-100) 
                    elif w_idx != previous_word_idx:
                        if w_idx < len(ner_chunk):
                            aligned_labels.append(ner_chunk[w_idx])
                        else:
                            aligned_labels.append(ner_label_dict["O"])
                        previous_word_idx = w_idx
                    else:
                        # Subword of the *same* word -> ignore for NER
                        aligned_labels.append(-100)
            
                sample = {
                    'input_ids': torch.tensor(encoding['input_ids']),
                    'attention_mask': torch.tensor(encoding['attention_mask']),
                    'labels_class': torch.tensor(label_class),
                    'labels_ner': torch.tensor(aligned_labels),
                    'word_ids': torch.tensor(transformed_word_ids)  
                }
                self.samples.append(sample)

    def __len__(self):
        return len(self.samples)
    
    def __getitem__(self, idx):
        return self.samples[idx]


train_df, temp_df = train_test_split(
    df, 
    test_size=0.3, 
    random_state=42, 
    stratify=df['labels']
)

val_df, test_df = train_test_split(
    temp_df, 
    test_size=0.5, 
    random_state=42, 
    stratify=temp_df['labels']
)
# -------------------------------
# Tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Datasets
train_dataset = NewsNERChunkedDataset(train_df, tokenizer)
val_dataset   = NewsNERChunkedDataset(val_df, tokenizer)
test_dataset  = NewsNERChunkedDataset(test_df, tokenizer)

# sample
sample = train_dataset[0]
ids = sample['input_ids'].tolist()
tokens = tokenizer.convert_ids_to_tokens(ids)
wids = sample['word_ids'].tolist()
nerlabs = sample['labels_ner'].tolist()

print("\n--- Sample Inspection ---")
print("Tokens:")
print(tokens)
print("\nTransformed Word IDs:")
print(wids)
print("\nAligned NER labels:")
print(nerlabs)



--- Sample Inspection ---
Tokens:
['[CLS]', 'ανεμος', 'σαι', '##νθ', 'στο', 'μεξικο', 'κερδισμενο', '##ς', 'ο', 'νορ', '##ις', 'κυριαρχια', 'της', 'ferrari', 'κυριαρχο', '##ς', 'σαι', '##νθ', 'και', 'κυριαρχη', 'ferrari', 'στο', 'μεξικο', '.', 'ο', 'ισπανος', ',', 'ο', 'οποιος', 'ετοιμαζεται', 'για', 'το', 'νεο', 'κεφαλαιο', 'της', 'καριερας', 'του', ',', 'τερματισε', 'πρωτος', 'στο', '19', '##ο', 'grand', 'prix', 'της', 'σεζον', ',', 'σημειωνοντας', 'τη', '2', '##η', 'νικη', 'του', '(', 'επειτα', 'απο', 'την', 'αυστραλια', ')', ',', 'στη', '2', '##η', 'νικη', 'της', 'ferrari', 'επειτα', 'απο', 'εκεινη', 'του', 'λε', '##κλε', '##ρ', 'που', 'τερματισε', '3', '##ος', '.', 'κερδισμενο', '##ς', 'βγηκε', 'ο', 'νορ', '##ις', ',', 'ο', 'οποιος', 'μειωσε', 'στους', '47', 'την', 'αποσταση', 'του', 'απο', 'τον', 'πρωτοπορο', 'φερ', '##στα', '##πεν', '.', 'ο', '27', '##χρονος', 'τερματισε', 'στην', '6', '##η', 'θεση', 'λογω', 'ποινη', '##ς', '20', 'δευτερολεπτ', '##ων', '.', 'διοτι', 'σε', 'κουρ